In [1]:
import numpy as np
import pandas as pd 
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import nltk 
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.model_selection import cross_val_score
from sklearn.metrics.pairwise import euclidean_distances
from collections import defaultdict

In [11]:
#dataset = pd.read_json('300-399.json')
#data1 = pd.read_json('400-499.json') 
#data2 = pd.read_json('0-200.json')
#data3 = pd.read_json('200-299.json')
#dataset = dataset.append(data1)  
#dataset = dataset.append(data2) 
#dataset = dataset.append(data3)   
dataset= pd.read_json('sample_0_10000_books_revised.json')

In [12]:
print (len(dataset.keys()))

6916


In [3]:
print (len(dataset.keys()))

7454


# Dictionary Index

In [4]:
vectorizer = TfidfVectorizer(stop_words='english' ,
                     binary=False,
                     max_df=0.95, 
                     min_df=0.02,
                     norm = 'l2')

In [5]:
# create a list of reviews rather than creating a list of list 
#dictionary for each keys 
#need to create it in one list but is not creating in one list 


#key : title #value : string of all 10 reviews in one string 
onlyreviews = defaultdict(str) 
for keys in dataset.keys():
    #keys = keys.encode('UTF8')
    keyreview = ""
   
    datasets = dataset[keys]['review'] 
    #print(type(datasets))
   
    for i in datasets :  
        if type(i)!= float : 
         
            keyreview = keyreview + i[0].encode('UTF8')             
    keys = keys.encode('UTF8') 
    onlyreviews[keys] = keyreview
print(type(onlyreviews["A Book of Common Prayer"]) ) 


<type 'str'>


In [377]:
book_array = onlyreviews.keys()

book_to_index= {book : i for i, book in enumerate(book_array)}

index_to_book = {i : book for i, book in enumerate(book_array)}

review_vectors = vectorizer.fit_transform([onlyreviews[keys] for keys in onlyreviews]).toarray()
#Need to tokenize from the vectors

In [378]:
#print(review_vectors.shape)

#print(len(vectorizer.vocabulary_))  
#print(review_vectors)

print(vectorizer.get_feature_names()) 
#creating vectorization 
#title and index connect array 
# and words enumerations 


[u'10', u'100', u'11', u'12', u'13', u'15', u'20', u'200', u'2012', u'2016', u'2017', u'20th', u'30', u'300', u'400', u'50', u'_blank', u'ability', u'able', u'absolute', u'absolutely', u'account', u'action', u'actual', u'actually', u'add', u'admit', u'adult', u'adventure', u'adventures', u'advice', u'age', u'ages', u'ago', u'agree', u'al', u'albums', u'alt', u'amazing', u'america', u'american', u'amp', u'analysis', u'ancient', u'answer', u'apparently', u'appreciate', u'approach', u'aren', u'art', u'ask', u'asked', u'aspects', u'attempt', u'attention', u'audience', u'audio', u'author', u'authors', u'aware', u'away', u'awesome', u'background', u'bad', u'based', u'basic', u'basically', u'beautiful', u'beautifully', u'beauty', u'began', u'begin', u'beginning', u'begins', u'believe', u'best', u'better', u'bible', u'big', u'biography', u'bit', u'black', u'blockquote', u'body', u'book', u'books', u'boring', u'born', u'bought', u'boy', u'br', u'brain', u'break', u'brief', u'brilliant', u'bring

# Cosine Similarity Matrix Using Book Title and similarity Matrix 


In [379]:
#similarity Matrix Creation 
def get_sim(book1, book2, input_doc_mat, book_to_index):
    """Returns a float giving the cosine similarity of 
       the two movie transcripts.
    
    Params: {book1: String,
             book2: String,
             input_doc_mat: Numpy Array,
             movie_to_index: Dict}
    Returns: Float (Cosine similarity of the two movie transcripts.)
    """
    # YOUR CODE HERE

    book1idx = book_to_index[book1] 
    book2idx = book_to_index[book2] 
    
    mat1 = input_doc_mat[book1idx] 
    mat2 = input_doc_mat[book2idx] 
    num = np.dot(mat1, mat2) 
    
    onenorm  = np.sqrt(np.sum(np.square(mat1))) 
    twonorm = np.sqrt(np.sum(np.square(mat2)))  
    
    denum = onenorm * twonorm 
     
    cosine = num/denum
    
    return cosine


In [380]:
def build_book_sims_cos(n_books,index_to_book,input_doc_mat,book_to_index,input_get_sim_method):
    """Returns a movie_sims matrix of size (num_movies,num_movies) where for (i,j):
        [i,j] should be the cosine similarity between the movie with index i and the movie with index j
        
    Note: What you set the diagonal to doesn't really matter, 
    but you should set it to 1 to indicate that all movies are trivially perfectly similar to themselves.
    
    Params: {n_book: Integer,
             index_to_book: String,
             input_doc_mat: Numpy Array,
             movie_to_index: Dict,
             input_get_sim_method: Function}
    Returns: Numpy Array 
    """
    # YOUR CODE HERE
    #hopefully this is okay! I guess 
    returnarray = np.zeros((n_books, n_books))
    for i in range(n_books) : 
        iname = index_to_book[i]  
        for j in range(i): 
            jname = index_to_book[j] 
            number = input_get_sim_method(iname, jname, input_doc_mat, book_to_index)
            returnarray[i][j] = number 
            returnarray[j][i] = number 
        returnarray[i][i] = 1.0 
    return returnarray

            

In [381]:
#create cosine matrix 
num_books = len(index_to_book)
books_list = dataset.keys() 
book_sims_cos = build_book_sims_cos(num_books, index_to_book, review_vectors, book_to_index, get_sim)

/Library/Frameworks/Python.framework/Versions/2.7/lib/python2.7/site-packages/ipykernel_launcher.py:26: RuntimeWarning: invalid value encountered in double_scalars


In [382]:
#draw the matrix by the matlib 
assert type(book_sims_cos) == np.ndarray
assert book_sims_cos.shape == (num_books,num_books)


# Print top Ten books similar to the given book  reviews

In [383]:
#similarity measure print top ten that are related to one another 
#top ten similarity of the books related to the books that are given 


In [384]:
#import matplotlib.pyplot as plt

#plt.imshow(book_sims_cos , interpolation='none',
      #     cmap=plt.cm.Greys)
#plt.colorbar()

#plt.xticks(range(num_books),books_list , rotation=90)
#plt.yticks(range(num_books), books_list)
#plt.show()


In [393]:
def get_ranked_books(book, matrix):
    """
    Return sorted rankings (most to least similar) of movies as 
    a list of two-element tuples, where the first element is the 
    movie name and the second element is the similarity score
    
    Params: {book: String,
             matrix: np.ndarray}
    Returns: List<Tuple>
    """
    
    # Get movie index from movie name
    book_idx = book_to_index[book]
    
    # Get list of similarity scores for movie
    score_lst = matrix[book_idx]
    book_score_lst = [(index_to_book[i], s) for i,s in enumerate(score_lst)]
    
    # Do not account for movie itself in ranking
    book_score_lst = book_score_lst[:book_idx] + book_score_lst[book_idx+1:]
    
    # Sort rankings by score
    book_score_lst = sorted(book_score_lst, key=lambda x: -x[1])
    
    return book_score_lst


def print_top(book, matrix, sim_type, k=10):
    """
    Print the k most and least similar movies to 'star wars'
    
    Params: {book: String,
             matrix: np.ndarray,
             sim_type: String,
             k: Integer}
    Returns: None
    """
    
    book_score_lst = get_ranked_books(book, matrix)
    
    print("Top {} most similar books to {} [{}]".format(k, book , sim_type))
    print("======")
    for (book, score) in book_score_lst[:k]:
        print("%.3f %s" % (score, book))

    print()
    
    print("Top {} least similar books to {} [{}]".format(k, book , sim_type))
    print("======")
    for (book, score) in book_score_lst[-k:][::-1]:
        print("%.3f %s" % (score, book))

In [394]:
print_top('The Lord of the Rings (The Lord of the Rings, #1-3) (by) J.R.R. Tolkien (published by) Recorded Books', book_sims_cos, 'cosine sim')

Top 10 most similar books to The Lord of the Rings (The Lord of the Rings, #1-3) (by) J.R.R. Tolkien (published by) Recorded Books [cosine sim]
0.675 A Great and Terrible Beauty (Gemma Doyle, #1) (by) Libba Bray (published by) Simon and Schuster
0.443 The Woman in White (by) Wilkie Collins (published by) Barnes  Noble Classics
0.416 Howards End (by) E.M. Forster (published by) Dover Publications
0.313 Kafka on the Shore (by) Haruki Murakami (published by) Audiofy/Naxos
0.279 QED: The Strange Theory of Light and Matter (by) Richard Feynman (published by) Princeton University Press
0.251 The Confessions (by) Augustine of Hippo (published by) Hendrickson
0.226 The Devil Wears Prada (by) Lauren Weisberger (published by) Broadway
0.206 The Curious Incident of the Dog In the Night-time (by) Mark Haddon (published by) Red Fox
0.206 Hamlet (by) William Shakespeare (published by) Simon  Schuster
0.206 Drageløberen (by) Khaled Hosseini (published by) Cicero
()
Top 10 least similar books to Drage

In [265]:
# Evaluation Check whether the books exist in the book dictionary 
#book 

In [389]:
book_array = onlyreviews.keys() 
print(book_array)
lstofbooks = [u'Child of the Prophecy (Sevenwaters, #3)',
  u'Gregor and the Marks of Secret (Underland Chronicles, #4)',
  u'Emperor Mage (Immortals, #3)',
  u"The Queen of Attolia (The Queen's Thief, #2)",
  u"The Wizard's Dilemma (Young Wizards, #5)",
  u'Awakening (Sweep, #5)',
  u'A Ring of Endless Light (Austin Family, #4)',
  u'A Muralha de Gelo (As Cr\xf3nicas de Gelo e Fogo #2)',
  u'Black Heart (Curse Workers, #3)',
  u'The Indigo Spell (Bloodlines, #3)',
  u'The Atlantis Complex (Artemis Fowl, #7)',
  u"The Demon's Covenant (The Demon's Lexicon, #2)",
  u'Syren (Septimus Heap, #5)',
  u'Haunted (The Mediator, #5)',
  u'The Farthest-Away Mountain',
  u'Dark Whispers (Unicorn Chronicles, #3)',
  u'Curse of the Blue Tattoo: Being an Account of the Misadventures of Jacky Faber, Midshipman and Fine Lady (Bloody Jack, #2)',
  u'The Subtle Knife (His Dark Materials, #2)']  
newlstofbooks = [] 

for k in lstofbooks :  
    newlstofbooks.append(k.encode('UTF8'))

    
for k in newlstofbooks : 
    if k in book_array : 
        print(True)
        
if 'Caesar (Masters of Rome, #5) (by) Colleen McCullough (published by) Avon' in book_array : 
    print(True)

     

['Caesar (Masters of Rome, #5) (by) Colleen McCullough (published by) Avon', 'El Mundo Perdido (Parque Jur\xc3\xa1sico, #2) (by) Michael Crichton (published by) DeBolsillo (Espa\xc3\xb1a)', 'Picnics in the Park: Moveable Feasts for Dining Alfresco (by) Connie McCole (published by) Hearst Communications', 'A Prayer for Owen Meany (by) Irving John (published by) Bloomsbury Publishing PLC', 'Introducing the Little Prince: Board Book Gift Set (by) Antoine de Saint-Exup\xc3\xa9ry (published by) Houghton Mifflin', "Papillions (by) Jacklyn E. Hungerland (published by) Barron's Educational Series", 'The Curious Incident of the Dog In the Night-time (by) Mark Haddon (published by) Red Fox', 'Fabeln. Text/ Kommentar. (Lernmaterialien) (by) Phaedrus (published by) Buchner', 'The Nature of Space and Time (by) Stephen Hawking (published by) Princeton University Press', 'Laura Ingalls Wilder: Pioneer and Author : Biographies for Young Readers (by) William Anderson (published by) Kipling Pr', 'A Guid

# Cosine Similarity Based on Description 


In [22]:
for k in dataset.keys():
    if dataset[k]['description'] == None and dataset[k]['review'] == []:
        print("no")

no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no
no


In [21]:
dataset

Palm Sunday/Welcome to the Monkeyhouse (by) Kurt Vonnegut (published by) Vintage  \
author                                              Kurt Vonnegut                                  
average_rating                                               4.17                                  
description                                                  None                                  
image           https://s.gr-assets.com/assets/nophoto/book/11...                                  
review          [[\n      Oh wow! I finished it! Almost three ...                                  
review_count                                                   11                                  
similar_books   [A Life in Letters, Foreign Correspondence: A ...                                  

               "A" Is for Zebra (by) Mark Shulman (published by) Sterling  \
author                                               Mark Shulman           
average_rating                                               3.68           
description     <b>Mark Shulman and Tamara Petrosino return wi...           
image           https://images.gr-assets.com/books/1328858765m...           
review          [[\n      At first I didn't get this book. But...           
review_count                                                   20           
similar_books                                                  []           

               "B" Is for Betsy (by) Carolyn Haywood (published by) HMH Books for Young Readers  \
author                                            Carolyn Haywood                                 
average_rating                                               4.02                                 
description     Carolyn Haywood's stories about her irrepressi...                                 
image           https://s.gr-assets.com/assets/nophoto/book/11...                                 
review          [[\n      From the cover, I was expecting a mo...                                 
review_count                                                  110                                 
similar_books   [More Stories from Grandma's Attic (Grandma's ...                                 

               "Fabulae Novae" Di Fedro (by) Phaedrus (published by) M. Solfanelli  \
author                                                   Phaedrus                    
average_rating                                               3.52                    
description     Fedro e Aviano sono gli unici autori della let...                    
image           https://s.gr-assets.com/assets/nophoto/book/11...                    
review          [[\n      Instruire et amuser, les deux fins d...                    
review_count                                                    0                    
similar_books   [Menander: The Plays and Fragments, History of...                    

               "Stand Back," Said the Elephant, "I'm Going to Sneeze!" (by) Patricia Thomas (published by) William Morrow & Company, Inc.  \
author                                            Patricia Thomas                                                                           
average_rating                                               4.38                                                                           
description     Knowing the havoc it will cause, all the anima...                                                                           
image           https://s.gr-assets.com/assets/nophoto/book/11...                                                                           
review          [[\n      The elephant, of course, is going to...                                                                           
review_count                                                  113                                                                           
similar_books   [One-Dog Canoe, Millie Waits for the Mail, A P...                                                                

In [ ]:
onlydescs = defaultdict(str) 
for k in dataset.keys():
#     k = k.encode('UTF8')
    title = k.split('(by)')[0]
    if dataset[k]['description'] is not None:
        onlydescs[title] = dataset[k]['description'] 


In [ ]:
vectorizer = TfidfVectorizer(stop_words='english' ,
                     binary=False,
                      max_df=0.95, 
                      min_df=3,
                     norm = 'l2')

In [ ]:
book_array = onlydescs.keys()

book_to_index= {book : i for i, book in enumerate(book_array)}

index_to_book = {i : book for i, book in enumerate(book_array)}

review_vectors = vectorizer.fit_transform([onlydescs[keys] for keys in onlydescs]).toarray()
#Need to tokenize from the vectors

In [ ]:
print(len(vectorizer.get_feature_names()))

In [43]:
#description TFIDF Vectorizer 
# create a list of reviews rather than creating a list of list 
#dictionary for each keys 
#need to create it in one list but is not creating in one list 


#key : title #value : string of all 10 reviews in one string 
onlydescription = defaultdict(str) 
for keys in dataset.keys():
    #keys = keys.encode('UTF8')
    #keyreview = ""
    description = dataset[keys]['description']
    
    print(type(description)) 
    #print(type(description )) 
    #print(description)
    print("First Key")
    print(keys)
    print(description) 
    #for i in description : 
       # print(i) 
       # if type(i)!= float :  
            
   # keyreview = ""
   ## datasets = dataset[keys]['review']
   # for i in datasets :  
       
         #   for item in i :
         #       keyreview 
         #       for k in item: 
    
       #             keyreview = keyreview + k 
   # keyreview = keyreview.encode('UTF8') 
   # keys = keys.encode('UTF8')
   # onlyreviews[keys] = keyreview



#for k in onlyreviews["A Book of Common Prayer"] : 
 #   print(k)


<type 'NoneType'>
First Key
 Palm Sunday/Welcome to the Monkeyhouse (by) Kurt Vonnegut (published by) Vintage
None
<type 'unicode'>
First Key
"A" Is for Zebra (by) Mark Shulman (published by) Sterling
<b>Mark Shulman and Tamara Petrosino return with a fabulous follow-up to last season’s <i>AA is for Aardvark</i>. And it’s got a clever new twist. </b><br /><br /> <br /><br />The alphabetic antics continue—starting from the end! That’s why <i>A</i> is for <i>zebrA </i>and <i>Z</i> is for <i>jazZ</i>, and nothing’s what you’d expect. The featured letter doesn’t appear just once—it’s sprinkled throughout the hilarious illustrations. The <i>I</i> page not only has <i>sushI</i>, there’s <i>delI</i>, <i>spaghettI</i>, <i>graffitI</i>, and <i>khakI</i>, too. And if you think working backwards makes it easier, well, just try to come up with words that end in Q or J! The results can be quite surprising!<br /><br />Teachers, librarians, parents, and kids will love the silly—but smart—acrobatics i

<type 'unicode'>
First Key
A Guided Tour of 5 Works by Plato: Euthyphro/Apology/Crito/Phaedo/Cave (by) Christopher Biffle (published by) Mayfield Publishing Company (NY)
Offering a study of five Plato dialogues, this book takes students through a variety of creative questions and tasks, aiming to help them to develop their critical thinking and reading and writing skills. Annotation tasks in the margins invite students to underline key sentences, paraphrase main ideas, or supply original illustrative examples. A chapter gives advice on writing about Plato's works, and an appendix new to this edition provides a brief overview of epistemology, metaphysics and ethics.
<type 'unicode'>
First Key
A Heartbreaking Work of Staggering Genius (by) Dave Eggers (published by) Vintage
'When you read his extraordinary memoir you don't laugh, then cry, then laugh again; you somehow experience these emotions all at once.'<br /><br />"Well, this was when Bill was sighing a lot. He had decided that afte

<type 'NoneType'>
First Key
A Primer of Conservation Biology (by) Richard B. Primack (published by) Sinauer Associates
None
<type 'unicode'>
First Key
A Psychonaut's Guide to the Invisible Landscape: The Topography of the Psychedelic Experience (by) Dan Carpenter (published by) Park Street Press
A bold cartography of the inner landscape visible only to those experiencing altered states<br /><br />• Presents the psychedelic experience as an objective landscape that embodies the Other, rather than a subjective state of mind<br /><br />• Provides corroboration of phenomena encountered by those who venture into this domain<br /><br />Journeying into the invisible world revealed by his use of the dissociative psychedelic DXM (dextromethorphan), Dan Carpenter found that what he experienced was not simply subjective sensations and psychological states but an objective world of familiar, if inordinately odd, landmarks and characters. The running diary he kept of these voyages recounts impressi

Act of Will (by) Barbara Taylor Bradford (published by) St. Martin's Griffin
<i>From beloved bestselling author Barbara Taylor Bradford comes the enthralling saga of three generations of extraordinary women--of the fate that befalls them, and the choices that define their lives…<br /><br /></i><b>IN THE NAME OF LOVE.</b><br />Orphaned after the death of her mother, well-bred Audra Kenton rose from selfless nurse to servant of an affluent suffragette, to a fiercely independent bride whose passionate marriage was overtaken by an unforeseeable tragedy. Now Audra has but one dream--to bestow upon her brilliantly artistic daughter, every opportunity that she was denied…<br /><br /><b>AT THE HEART OF AMBITION.</b><br />Given the world, the stubborn Christina has forsaken the wishes of her noble mother to forge the career of her choice--that of a glittering Manhattan fashion empire she hopes to bequeath to her own daughter. But in young and beautiful Kyle stirs a spirit that is inherently hea

<type 'unicode'>
First Key
All Families are Psychotic (by) Douglas Coupland (published by) Bloomsbury USA
<div>The most disastrous family reunion in the history of fiction.<br /><br />The Drummond family, reunited for the first time in years, has gathered near Cape Canaveral to watch the launch into space of their beloved daughter and sister, Sarah. Against the Technicolor unreality of Florida's finest tourist attractions, the Drummonds stumble into every illicit activity under the tropical sun-kidnapping, blackmail, gunplay, and black market negotiations, to name a few. But even as the Drummonds' lives spin out of control, Coupland reminds us of their humanity at every turn, hammering out a hilarious masterpiece with the keen eye of a cultural critic and the heart and soul of a gifted storyteller. He tells not only the characters' stories but also the story of our times--thalidomide, AIDS, born-again Christianity, drugs, divorce, the Internet-all bound together with the familiar glue 

...

<type 'unicode'>
First Key
The Rapture of Canaan (by) Sheri Reynolds (published by) Berkley Books
<b>Oprah Book Club® Selection, April 1997</b>: Members of the Church of Fire and Brimstone and God's Almighty Baptizing Wind spend their days and nights serving the Lord and waiting for the Rapture--that moment just before the Second Coming of Christ when the saved will be lifted bodily to heaven and the damned will be left behind to face the thousand years of tribulation on earth. The tribulation, according to Grandpa Herman, founder of Fire and Brimstone, will be an ugly time: "He said that we'd run out of food. That big bugs would chase us around and sting us with their tails . . . He said we'd turn on the faucet in the bathroom and find only blood running out . . . He said evil multitudes would come unto us and cut off our limbs, and that we wouldn't die . . . And then he'd say, 'But you don't have to be left behind. You can go straight to Heaven with all of God's special children if y

Roland, The Last Gunslinger, moves ever closer to The Dark Tower of his dreams and nightmares—as he crosses a desert of damnation in a macabre world that is a twisted image of our own. With him are those he has drawn to this world: street-smart Eddie Dean and courageous wheelchair-bound Susannah.<br /><br />Ahead of him are mind-rending revelations about who and what is driving him. Against him is arrayed a swelling legion of foes—both more and less than human....
<type 'unicode'>
First Key
The Watcher and Other Stories (by) Italo Calvino (published by) Houghton Mifflin
<b>Alternate cover edition can be found <a href="https://www.goodreads.com/book/show/26124270-the-watcher-and-other-stories" rel="nofollow">here</a>. </b><br /><br />In "The Watcher," a member of the Communist Party is assigned to a polling place in Turin's Hospital for Incurables, where he observes the rejects of humanity and a grotesque parody of the democratic process. "Smog" anticipates a preoccupation with pollutio

First Key
Transgender Emergence: Therapeutic Guidelines for Working with Gender-Variant People and Their Families (by) Arlene Istar Lev (published by) Routledge
Explore an ecological strength-based framework for the treatment of gender-variant clients<br /><br />This comprehensive book provides you with a clinical and theoretical overview of the issues facing transgendered/transsexual people and their families. Transgender Emergence: Therapeutic Guidelines for Working with Gender-Variant People and Their Families views assessment and treatment through a nonpathologizing lens that honors human diversity and acknowledges the role of oppression in the developmental process of gender identity formation.<br /><br />Specific sections of Transgender Emergence: Therapeutic Guidelines for Working with Gender-Variant People and Their Families address the needs of gender-variant people as well as transgender children and youth. The issues facing gender-variant populations who have not been the fo

<type 'unicode'>
First Key
What Every Fidelity Investor Needs to Know (by) James Lowell (published by) Wiley
Fidelity offers investors some of the most innovative financial tools, products, and platforms currently available, and with <i>What Every Fidelity Investor Needs to Know, </i> James Lowell--one of the most trusted names in the investment business and a self-described Fidelity fanatic--will help you get the best out of what Fidelity has to offer; whether it be through taxable accounts, IRAs, or 401(k)s.
<type 'unicode'>
First Key
What Every Investor Needs to Know about Accounting Fraud (by) Jeff Madura (published by) McGraw-Hill Companies
Explains common accounting maneuvers, distortions, and outright deceptions that savvy investors must be able to recognize. This book provides investors with: methods for uncovering scams that distort revenues, hide expenses; studies of infamous accounting frauds and how they could have been avoided; a zero-tolerance investing code, and more.
<t

<type 'unicode'>
First Key
eBay Business All-in-One Desk Reference for Dummies (by) Marsha Collier (published by) Wiley
Bestselling author Marsha Collier presents readers with an all-new guide that goes beyond all previous eBay business books, offering one-stop guidance on eBay techniques as well as entrepreneurial fundamentals. She provides in-depth coverage on the most critical eBay topics, including merchandise sourcing, marketing, advertising, and customer service.<br />The minibooks that make up the guide cover eBay registration, navigation, and buying; getting ready to sell; digital photography and scanning for sales pages; eBay selling and marketing; getting legal and licensed; using auction management software; setting up an office (PCs, Internet, networking, and shipping); and PayPal.<br />* Marsha Collier's eBay books have sold hundreds of thousands of copies and her Starting an eBay Business For Dummies is currently the bestselling eBay reference on the market<br />* This on